# Italian Day-Ahead prices

In [1]:
import glob
import math
from datetime import datetime

import pandas as pd
import plotly.express as px
import plotly.graph_objects as go

### Concat xlsx sheets

In [2]:
paths = glob.glob('../data/raw_data/historic_prices/*')
price_df_list = []
for path in paths:
    price_df_list.append(pd.read_excel(path, sheet_name='Prezzi-Prices'))

price_df = pd.concat(price_df_list, axis=0)
price_df.rename({'   Data/Date\n(YYYYMMDD)': 'date', 'Ora\n/Hour': 'hour'}, axis=1, inplace=True)
price_df.date = pd.to_datetime(price_df.date, format='%Y%m%d').dt.normalize()
price_df = price_df.loc[price_df.hour <= 24]
price_df = price_df.sort_values(['date', 'hour']).reset_index(drop=True)
price_df.to_csv('../data/clean_data/wholesale_price.csv')
price_df

date  hour        PUN       AUST        BSP       CNOR       COAC  \
0     2019-01-01     1   51.00000   51.00000   51.00000   51.00000   51.00000   
1     2019-01-01     2   46.27000   46.27000   46.27000   46.27000   46.27000   
2     2019-01-01     3   39.78000   39.78000   39.78000   39.78000   39.78000   
3     2019-01-01     4   27.86938   27.86938   27.86938   27.86938   27.86938   
4     2019-01-01     5   22.00000   22.00000   22.00000   22.00000   22.00000   
...          ...   ...        ...        ...        ...        ...        ...   
35055 2022-12-31    20  333.00000  333.00000  333.00000  333.00000  333.00000   
35056 2022-12-31    21  310.00000  310.00000  310.00000  310.00000  310.00000   
35057 2022-12-31    22  270.00000  270.00000  270.00000  270.00000  270.00000   
35058 2022-12-31    23  217.78000  217.78000  217.78000  217.78000  217.78000   
35059 2022-12-31    24  200.00000  200.00000  200.00000  200.00000  200.00000   

            CORS       CSUD       FRAN  ...      ROSN       SARD       SICI  \
0       51.00000   51.00000   51.00000  ...  51.00000   51.00000   51.00000   
1       46.27000   46.27000   46.27000  ...  46.27000   46.27000   46.27000   
2       39.78000   39.78000   39.78000  ...  39.78000   39.78000   39.78000   
3       27.86938   27.86938   27.86938  ...  27.86938   27.86938   27.86938   
4       22.00000   22.00000   22.00000  ...  22.00000   22.00000   22.00000   
...          ...        ...        ...  ...       ...        ...        ...   
35055  333.00000  333.00000  333.00000  ...       NaN  333.00000  333.00000   
35056  310.00000  310.00000  310.00000  ...       NaN  310.00000  310.00000   
35057  270.00000  270.00000  270.00000  ...       NaN  270.00000  270.00000   
35058  217.78000  217.78000  217.78000  ...       NaN  217.78000  217.78000   
35059  200.00000  200.00000  200.00000  ...       NaN  200.00000  200.00000   

            SLOV        SUD       SVIZ       XAUS       XFRA    CALA    XGRE  
0       51.00000   51.00000   51.00000   51.00000   51.00000     NaN     NaN  
1       46.27000   46.27000   46.27000   46.27000   46.27000     NaN     NaN  
2       39.78000   39.78000   39.78000   39.78000   39.78000     NaN     NaN  
3       27.86938   27.86938   27.86938   27.86938   27.86938     NaN     NaN  
4       22.00000   22.00000   22.00000   22.00000   22.00000     NaN     NaN  
...          ...        ...        ...        ...        ...     ...     ...  
35055  333.00000  333.00000  333.00000  333.00000  333.00000  333.00  333.00  
35056  310.00000  310.00000  310.00000  310.00000  310.00000  310.00  310.00  
35057  270.00000  270.00000  270.00000  270.00000  270.00000  270.00  270.00  
35058  217.78000  217.78000  217.78000  217.78000  217.78000  217.78  217.78  
35059  200.00000  200.00000  200.00000  200.00000  200.00000  200.00  200.00  

[35060 rows x 24 columns]

### Convert UK data to EUR and merge

In [3]:
epex_price_df = pd.read_csv('../data/raw_data/EPEX_and_N2EX_DA_WD_PRICES.csv')[['SETTLEMENT_DATE', 'SETTLEMENT_PERIOD', 'EPEX_HH_DA']]
epex_price_df.columns = ['date', 'hour', 'gb_price_gbp']
epex_price_df.drop_duplicates(subset=['date', 'hour'], inplace=True)
epex_price_df.date = pd.to_datetime(epex_price_df.date)
conversion_df = pd.read_csv('../data/raw_data/euro-british-pound-exchange-rate-historical-chart.csv', skiprows=15)
conversion_df.rename({' value': 'conversion'}, axis=1, inplace=True)
conversion_df.date = pd.to_datetime(conversion_df.date)
conversion_df = pd.merge(pd.DataFrame(pd.date_range(start='2022-01-01', end='2022-12-31', freq='D'), columns=['date']), conversion_df, on='date', how='left').fillna(method='ffill')
epex_price_df = pd.merge(epex_price_df, conversion_df, on='date', how='left')
epex_price_df['gb_price_eur'] = epex_price_df.gb_price_gbp / epex_price_df.conversion
epex_price_df = epex_price_df.round(2)
epex_price_df.drop(['gb_price_gbp', 'conversion'], axis=1, inplace=True)
epex_price_df

date  hour  gb_price_eur
0     2022-01-01     1         89.24
1     2022-01-01     2         89.24
2     2022-01-01     3        108.52
3     2022-01-01     4         57.12
4     2022-01-01     5         83.29
...          ...   ...           ...
17515 2022-12-31    44        145.82
17516 2022-12-31    45        152.25
17517 2022-12-31    46        102.63
17518 2022-12-31    47         45.11
17519 2022-12-31    48         19.62

[17520 rows x 3 columns]

In [4]:
price_df = pd.merge(price_df, epex_price_df, on=['date', 'hour'], how='left')
price_df.head()

date  hour       PUN      AUST       BSP      CNOR      COAC  \
0 2019-01-01     1  51.00000  51.00000  51.00000  51.00000  51.00000   
1 2019-01-01     2  46.27000  46.27000  46.27000  46.27000  46.27000   
2 2019-01-01     3  39.78000  39.78000  39.78000  39.78000  39.78000   
3 2019-01-01     4  27.86938  27.86938  27.86938  27.86938  27.86938   
4 2019-01-01     5  22.00000  22.00000  22.00000  22.00000  22.00000   

       CORS      CSUD      FRAN  ...      SARD      SICI      SLOV       SUD  \
0  51.00000  51.00000  51.00000  ...  51.00000  51.00000  51.00000  51.00000   
1  46.27000  46.27000  46.27000  ...  46.27000  46.27000  46.27000  46.27000   
2  39.78000  39.78000  39.78000  ...  39.78000  39.78000  39.78000  39.78000   
3  27.86938  27.86938  27.86938  ...  27.86938  27.86938  27.86938  27.86938   
4  22.00000  22.00000  22.00000  ...  22.00000  22.00000  22.00000  22.00000   

       SVIZ      XAUS      XFRA  CALA  XGRE  gb_price_eur  
0  51.00000  51.00000  51.00000   NaN   NaN           NaN  
1  46.27000  46.27000  46.27000   NaN   NaN           NaN  
2  39.78000  39.78000  39.78000   NaN   NaN           NaN  
3  27.86938  27.86938  27.86938   NaN   NaN           NaN  
4  22.00000  22.00000  22.00000   NaN   NaN           NaN  

[5 rows x 25 columns]

### Plot data

In [5]:
fig = go.Figure()

fig.add_trace(go.Scatter(
    x=price_df.date,
    y=price_df.PUN,
    name='Hourly',
    line=dict(color='slategrey', width=0.5)
))
fig.add_trace(go.Scatter(
    x=price_df.date,
    y=price_df.PUN.rolling(336).mean(),
    name='2 week ave.',
    line=dict(color='mediumvioletred', width=2.5)
))

fig.update_layout(
    title='National Price (PUN) - buy price',
    yaxis_title='€/MWh',
    width=1200,
    height=400,
    template='ggplot2'
)

fig.write_image('../figures/historic-pun.jpeg', scale=5, engine='orca')
fig

### 2022 data

In [6]:
price_df_22 = price_df.loc[price_df.date >= datetime(2022, 1, 1)].reset_index(drop=True)
price_df_22['datetime'] = pd.to_datetime((price_df_22.date.astype(str) + (price_df_22.hour - 1).astype(str) + ''), format='%Y-%m-%d%H')
price_df_22.sort_values('datetime', inplace=True)
price_df_22.to_csv('../data/clean_data/wholesale_price_2022.csv')
price_df_22.head()

date  hour     PUN    AUST     BSP    CNOR   COAC    CORS    CSUD  \
0 2022-01-01     1  170.28  170.28  170.28  170.28  250.0  170.28  170.28   
1 2022-01-01     2  155.72  155.72  155.72  155.72  250.0  155.72  155.72   
2 2022-01-01     3  147.09  147.09  147.09  147.09  250.0  147.09  147.09   
3 2022-01-01     4   91.00   91.00   91.00   91.00  250.0   91.00   91.00   
4 2022-01-01     5  104.00  104.00  104.00  104.00  250.0  104.00  104.00   

     FRAN  ...    SICI    SLOV     SUD    SVIZ    XAUS    XFRA    CALA  \
0  170.28  ...  170.28  170.28  170.28  170.28  170.28  170.28  170.28   
1  155.72  ...  155.72  155.72  155.72  155.72  155.72  155.72  155.72   
2  147.09  ...  147.09  147.09  147.09  147.09  147.09  147.09  147.09   
3   91.00  ...   91.00   91.00   91.00   91.00   91.00   91.00   91.00   
4  104.00  ...  104.00  104.00  104.00  104.00  104.00  104.00  104.00   

     XGRE  gb_price_eur            datetime  
0  170.28         89.24 2022-01-01 00:00:00  
1  155.72         89.24 2022-01-01 01:00:00  
2  147.09        108.52 2022-01-01 02:00:00  
3   91.00         57.12 2022-01-01 03:00:00  
4  104.00         83.29 2022-01-01 04:00:00  

[5 rows x 26 columns]

In [7]:
fig = go.Figure()

fig.add_trace(go.Scatter(
    x=price_df_22.date,
    y=price_df_22.gb_price_eur.rolling(12).mean(),
    name='GB EPEX DA',
    line=dict(color='cornflowerblue', width=1.5)
))
fig.add_trace(go.Scatter(
    x=price_df_22.date,
    y=price_df_22.PUN.rolling(12).mean(),
    name='Italian MGP',
    line=dict(color='red', width=1.5)
))

fig.update_layout(
    title='British vs Italian comparison 2022',
    yaxis_title='€/MWh',
    width=1200,
    height=500,
    template='ggplot2'
)

fig.write_image('../figures/gb-italy-2022.jpeg', scale=5, engine='orca')
fig

In [8]:
fig = px.bar(
    price_df_22.groupby('hour')['PUN'].mean(),
    color=price_df_22.groupby('hour')['PUN'].mean(),
    color_continuous_scale='solar',
    title='Average PUN of each hour 2022',
    labels={'value': '€/MWh', 'hour': 'Hour'}
    )

fig.update_layout(
    showlegend=False,
    width=1200,
    height=400,
    template='ggplot2',
)
fig.update_coloraxes(showscale=False)
    
fig.write_image('../figures/hour-pun-22.jpeg', scale=5, engine='orca')
fig

In [17]:
price_df_22['month'] = price_df_22.date.dt.month
price_df_winter = price_df_22.loc[(price_df_22.month <= 1) | (price_df_22.month >= 11)]

fig = px.bar(
    price_df_winter.groupby('hour')['PUN'].mean(),
    color=price_df_winter.groupby('hour')['PUN'].mean(),
    color_continuous_scale='solar',
    title='Average PUN of each hour 2022 Jan/Nov/Dec',
    labels={'value': '€/MWh', 'hour': 'Hour'}
    )

fig.update_layout(
    showlegend=False,
    width=1200,
    height=400,
    template='ggplot2',
)
fig.update_coloraxes(showscale=False)
    
fig.write_image('../figures/hour-pun-22-winter.jpeg', scale=5, engine='orca')
fig

In [19]:
price_df_22['month'] = price_df_22.date.dt.month
price_df_winter = price_df_22.loc[(price_df_22.month > 1) & (price_df_22.month < 11)]

fig = px.bar(
    price_df_winter.groupby('hour')['PUN'].mean(),
    color=price_df_winter.groupby('hour')['PUN'].mean(),
    color_continuous_scale='solar',
    title='Average PUN of each hour 2022 non-winter',
    labels={'value': '€/MWh', 'hour': 'Hour'}
    )

fig.update_layout(
    showlegend=False,
    width=1200,
    height=400,
    template='ggplot2',
)
fig.update_coloraxes(showscale=False)
    
fig.write_image('../figures/hour-pun-22-non-winter.jpeg', scale=5, engine='orca')
fig

In [9]:
fig = px.bar(
    price_df_22.groupby('hour')['gb_price_eur'].mean(),
    color=price_df_22.groupby('hour')['gb_price_eur'].mean(),
    color_continuous_scale='solar',
    title='Average GB price of each hour',
    labels={'value': '€/MWh', 'hour': 'Hour'}
    )

fig.update_layout(
    showlegend=False,
    width=1200,
    height=400,
    template='ggplot2',
)
fig.update_coloraxes(showscale=False)
    
# fig.write_image('../figures/hour-pun-22.jpeg', scale=5, engine='orca')
fig

In [10]:
price_df.columns

Index(['date', 'hour', 'PUN', 'AUST', 'BSP', 'CNOR', 'COAC', 'CORS', 'CSUD',
       'FRAN', 'GREC', 'MALT', 'MONT', 'NORD', 'ROSN', 'SARD', 'SICI', 'SLOV',
       'SUD', 'SVIZ', 'XAUS', 'XFRA', 'CALA', 'XGRE', 'gb_price_eur'],
      dtype='object')

In [11]:
zonal_average = price_df_22[['AUST', 'BSP', 'CNOR', 'COAC', 'CORS', 'CSUD', 'FRAN', 'GREC', 'MALT', 'MONT', 'NORD', 'SARD', 'SICI', 'SLOV', 'SUD', 'SVIZ', 'XAUS', 'XFRA', 'CALA', 'XGRE']].mean()
pun = price_df_22[['PUN']].mean().item()
bar_colours = ['forestgreen' if x > pun else 'firebrick' for x in zonal_average.values]

fig = px.bar(
    zonal_average,
    color_discrete_sequence=[bar_colours],
    labels={'value': '€/MWh', 'index': ''},
    title='2022 average zonal clearing price - sell price',
    )
fig.add_hline(
    y=price_df_22[['PUN']].mean().item(),
    line_width=3,
    line_dash='dash',
    line_color='black',
    )
fig.add_annotation(
    text=f'PUN: {round(pun, 2)}', 
    font=dict(size=16),
    align='center',
    showarrow=False,
    xref='paper',
    yref='paper',
    x=0.98,
    y=0.95,
    )

fig.update_layout(
    xaxis={'categoryorder': 'total descending'},
    showlegend=False,
    yaxis_range=[280, 310],
    width=1200,
    height=500,
    template='ggplot2'
)
fig.update_coloraxes(showscale=False)

fig.write_image('../figures/zonal-price.jpeg', scale=2, engine='orca')
fig